# Practical: Linear Regression

Herman Kamper, 2023

## Preliminaries

In [ ]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt

## 1. Linear regression on simulated data

When implementing a new algorithm, it is useful to first develop it in a setting where you know what the answer should be. This helps to make sure that your implementation is correct before applying it in the (more complicated) setting where you actually want to use it. In this section we follow this principle by using simulated data where we have control over how the data is generated.

### 1.1. Simple linear regression

We start by developing our understanding of linear regression by using simulated data with one input variable. We use the simple linear regression model:

$$f(x; w_0, w_1) = w_0 + w_1x$$

In class we showed that the least squares estimates for the coefficients of this model is given by:

$$
\begin{align}
\hat{w}_0 &= \bar{y} - w_1\bar{x} \\
\hat{w}_1 &= \frac{\sum_{n = 1}^N (x^{(n)} - \bar{x})(y^{(n)}- \bar{y})}{\sum_{n = 1}^N (x^{(n)} - \bar{x})^2}
\end{align}
$$

where $\bar{x} = \frac{1}{N}\sum_{n = 1}^N x^{(n)}$ and similarly for $\bar{y}$.

Below we generate $N$ observations $\{ (x^{(n)}, y^{(n)}) \}_{n = 1}^N$ of inputs $x$ with corresponding outputs $y$. In the space provided, write the code to answer the following questions.

**Questions:**

- Plot the simulated data. You can use `plt.scatter`.
- Write code to determine the least squares estimates of $w_0$ and $w_1$ using the equations above.
- Plot a line showing this least squares fit.

In [ ]:
# Simulate data
N = 100
X = 2*np.random.rand(N, 1)
y = 4 + 3*X + np.random.randn(N, 1)

In [ ]:

# Answer: Add code and new cells here


If the input variables were multi-dimensional vectors $\mathbf{x}$, we could find the least squares estimate of the vector of weights $\mathbf{w}$ using

$$\hat{\mathbf{w}} = (\mathbf{X}^\top\mathbf{X})^{-1}\mathbf{X}^\top\mathbf{y}$$

**Question:** Implement this equation directly using NumPy to again find the least squares estimates $\hat{w}_0$ and $\hat{w}_1$. How do these values compare to those obtained above?  
*Hints:* Useful NumPy functions include `np.concatenate` (or the shorter `np.c_`), `np.dot` and `np.linalg.inv`. Remember to take special care to deal with the bias weight $w_0$.

In [ ]:

# Answer: Add code and new cells here


**Questions:**
    
- Go back to the top of Section 1.1, and change the number of simulated data points from $N = 100$ to $N = 1\,000\,000$. Then re-run all the cells.
- How does the estimated coefficients $\hat{w}_0$ and $\hat{w}_1$ now compare to the code used to generate the simulated data?
- How does the speed of the scalar implementation (start of Section 1.1) compare to that of the vectorised implementation (end of Section 1.1)?

### 1.2. Polynomial regression

We can extend standard linear regression to incorporate non-linear relationships by including polynomial features, sometimes referred to as *polynomial regression*. We can still use the linear regression code to fit this model, since the model is still linear in its parameters.

Consider the following model:

$$f(x; w_0, w_1) = w_0 + w_1x + w_2x^2$$

Below we generate a different dataset of $N$ observations $\{ (x^{(n)}, y^{(n)}) \}_{n = 1}^N$ of inputs $x$ with corresponding outputs $y$.

**Questions:**

- Plot the simulated data.
- Write code to determine the least squares estimates of $\mathbf{w}$.
- Plot a curve showing the least squares fit.

In [ ]:
N = 100
X = 6*np.random.rand(N, 1) - 3
y = 2 + X + 0.5 * X**2 + np.random.randn(N, 1)

In [ ]:

# Answer: Add code and new cells here


It is relatively easy to construct the polynomial functions using Python directly, but it might become cumbersome when dealing with multi-dimensional inputs and higher-order polynomial features. Luckily scikit-learn provides functionality for easily constructing high-degree polynomial features, for instance:

In [ ]:
from sklearn.preprocessing import PolynomialFeatures
poly_features = PolynomialFeatures(degree=2, include_bias=False)
X_poly = poly_features.fit_transform(X)
print("Original: ", X[0])
print("Polynomial: ", X_poly[0])

Scikit-learn also has functionality to directly fit a linear regression model, for instance:

In [ ]:
from sklearn.linear_model import LinearRegression
model = LinearRegression()
model.fit(X, y)
print("w_0: {:.4f}".format(model.intercept_[0]))
print("w_1: {:.4f}".format(model.coef_[0][0]))

The `LinearRegression` scikit-learn class is itself very similar to the NumPy function `np.linalg.lstsq`, which you could also call directly.

**Question:** Now fit a linear regression model with $20^{\text{th}}$ order polynomial features and plot the fit. You can use any of the scikit-learn functions or classes.

In [ ]:

# Answer: Add code and new cells here


**Questions:**

- Go back to the top of Section 1.2, and change the number of simulated data points from $N = 100$ to $N = 100\,000$. Then re-run all the cells.
- How does the estimated coefficients $\hat{w}_0$, $\hat{w}_1$ and $\hat{w}_2$ now compare to the code used to generate the simulated data?
- Does the additional data help when fitting the $20^{\text{th}}$ order polynomial features?
- Do you think additional data would help if we tried to fit the linear model $f(x; w_0, w_1) = w_0 + w_1x$ from Section 1.1 to the data in Section 1.2?

## 2. Linear regression on real data (with multiple variables)

The *Boston* dataset contains median house values for 506 neighbourhoods around Boston. We will try to predict house prices based on 13 input features. In the code below, the dataset is loaded directly using scikit-learn. More details of the 13 features are given [here](https://scikit-learn.org/stable/datasets/index.html#boston-dataset). You can use scikit-learn classes and functions throughout this section.

### 2.1. Load and visualise data

The cell below loads the data and plots a histogram of prices.

**Questions:**

- Create a scatter plot of "price" against "per capita crime rate" for all 506 neighbourhoods.
- Now divide the data into training and test sets, with the first 75% of the data used for training and the remaining 25% for testing.

In [ ]:
# Load data
import pandas as pd
import numpy as np
data_url = "http://lib.stat.cmu.edu/datasets/boston"
raw_df = pd.read_csv(data_url, sep="\s+", skiprows=22, header=None)
data = np.hstack([raw_df.values[::2, :], raw_df.values[1::2, :2]])
target = raw_df.values[1::2, 2]
X = data
y = target
feature_names = [
    "CRIM", "ZN", "INDUS", "CHAS", "NOX", "RM", "AGE",
     "DIS", "RAD", "TAX", "PTRATIO", "B", "LSTAT"
    ]

# Old data loading (you can see what happens when you do this):
# from sklearn.datasets import load_boston
# data = load_boston()
# feature_names = data.feature_names
# X = data.data
# y = data.target

# Histogram of prices
plt.hist(data.target)
plt.xlabel("Price ($1000s)")
plt.ylabel("Count")

In [ ]:

# Answer: Add code and new cells here


### 2.2. Simple linear regression

**Questions:**

- Perform simple linear regression where the input $x$ is `crime` and the output $y$ is `price`.
- Plot all the data.
- Plot only the training data.
- On both of the above plots, show the least squares fit.

In [ ]:

# Answer: Add code and new cells here


There are a number of ways to measure the performance of a regression model on held-out test data. The least squares approach itself uses a squared loss:

$$ J = \sum_{n = 1}^N \left(y^{(n)} - f(\mathbf{x}^{(n)}; \mathbf{w})\right)^2 $$

We can also calculate the *mean squared error* (MSE):

$$ \text{MSE} = \frac{1}{N} \sum_{n = 1}^N \left(y^{(n)} - f(\mathbf{x}^{(n)}; \mathbf{w})\right)^2 $$

or the *root-mean-square error* (RMSE):

$$ \text{RMSE} = \sqrt{ \frac{1}{N} \sum_{n = 1}^N \left(y^{(n)} - f(\mathbf{x}^{(n)}; \mathbf{w})\right)^2 } $$

**Questions:**

- Calculate the squared loss, MSE and RMSE metrics on the test data.
- Calculate the squared loss, MSE and RMSE metrics on the training data.

In [ ]:

# Answer: Add code and new cells here


### 2.3. Polynomial regression

**Questions:**

- Repeat Section 2.2 but now use $5^{\text{th}}$ order polynomial features.
- How do the metrics compare on the training and test data when using such a high-order polynomial?
- How do the trends in the metrics compare to that of the simple linear regression case in Section 2.2?

In [ ]:

# Answer: Add code and new cells here


**Optional question:** Go back and repeat Section 2.2 and 2.3 for the input feature "average number of rooms per dwelling". What do you observe? If you write your code carefully, you could probably make it easy to explore simple regression using any of the 13 features.

### 2.4. Multiple linear regression

**Questions:**

- Now perform multiple linear regression using all 13 features as the input $\mathbf{x}$ and the price as output $y$.
- Again calculate the squared loss, MSE and RMS on the training and test data.
- How does this compare to the models above?
- Print the values of each of the coefficients of the model.
- What do these coefficents tell us? For instance, what does it say about the relationship about `price` and `crime`? Or `price` and `rooms`?

In [ ]:

# Answer: Add code and new cells here


## Acknowledgements

I took parts of Section 2 of the practical from the [SciPy Lecture Notes](https://scipy-lectures.org/packages/scikit-learn/auto_examples/plot_boston_prediction.html).